In [1]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)

from astropy.time import Time
import h5py
from pycbc.conversions import mchirp_from_mass1_mass2,primary_mass,secondary_mass,chi_eff
import pylab,os,shutil
import matplotlib.pyplot as plt

from tqdm import tqdm
import uuid
import glob
from string import ascii_uppercase

# Select GW triggers

In [2]:
#4-OGC triggers are released in https://github.com/gwastro/4-ogc
gwfile = h5py.File('/work/ahnitz/WWW/4ogc/4-ogc.hdf')

#extract parameters
gwobs = np.array([obs.decode("utf-8") for obs in gwfile['trig'][:]])
name_gw = np.array([name.decode("utf-8") for name in gwfile['name'][:]],dtype='<U20')
#name_gw = np.array(gwfile['name'],dtype='<U20')

mass1 = np.array(gwfile['mass1'])
mass2 = np.array(gwfile['mass2'])
pmass = primary_mass(mass1,mass2)
smass = secondary_mass(mass1,mass2)

spin1z = np.array(gwfile['spin1z'])
spin2z = np.array(gwfile['spin2z'])
chieff = chi_eff(gwfile['mass1'][:], gwfile['mass2'][:],gwfile['spin1z'][:], gwfile['spin2z'][:])

ifar = np.array(gwfile['ifar'])
stat = np.array(gwfile['stat'])
time_gw = np.array(gwfile['time'])
    
def trigger(obrun='o3a',
            pmass=pmass,
            smass=smass,
            chieff=chieff,
            gwobs=gwobs,
            stat=stat,
            time_gw=time_gw):
    # convert the GW events name to UTF-8 format
    
    tO1_start = Time('2015-09-12T00:00:00')
    tO1_end = Time('2016-01-19T16:00:00')
    
    tO2_start = Time('2016-11-30T16:00:00')
    tO2_end = Time('2017-08-25T22:00:00')
    
    tO3a_start = Time('2019-04-01T15:00:00')
    tO3a_end = Time('2019-10-01T15:00:00')
    
    tO3b_start = Time('2019-11-01T15:00:00')
    tO3b_end = Time('2020-03-27T17:00:00')
    
    #seconday mass range in [1,3]
    lmass = smass <=3
    
    #total mass <= 10
    lmtotal = (pmass + smass) <=10
    
    #chi_eff in [-0.2,-0.2]
    lspin = (chieff<0.2) & (chieff>-0.2)
    
    #at least two detectors
    ltrig = (gwobs == 'HL') | (gwobs == 'HLV') | (gwobs == 'LV') | (gwobs == 'HV')
    
    #GW statistic >0
    lstat = stat>=0
    
    if obrun=='o1':
        ltime = (time_gw >= tO1_start.gps) & (time_gw<=tO1_end.gps)
    elif obrun=='o2':
        ltime = (time_gw >= tO2_start.gps) & (time_gw<=tO2_end.gps)
    elif obrun=='o3a':
        ltime = (time_gw >= tO3a_start.gps) & (time_gw<=tO3a_end.gps)
    elif obrun=='o3b':
        ltime = (time_gw >= tO3b_start.gps) & (time_gw<=tO3b_end.gps)
        
    l = lmass & lspin & ltrig & lstat & lmtotal & ltime
    print('There are ', l.sum(), ' triggers')
    
    # the index of a qualified GW event
    gwidx = np.where(l)[0]
    return gwidx

# Make a hdf file to store all GW candidates (with repeating name issues corrected)

In [33]:
with h5py.File('./gw_candidate_correct_repeating.hdf', 'w') as file:
    for o in ['o1','o2','o3a','o3b']:
        gwidx = trigger(obrun=o)
        # save the name_gw[trig] to a new np array, because it does not work to add an appendix to the name_gw[trig]
        trig_name_gw = name_gw[gwidx]
        # select the unique names and the count of repeating
        uniname, count = np.unique(trig_name_gw, return_counts=True)
        # duplicated elements are those with count >1
        duplicate = uniname[count>1]
        for dup_name in duplicate:
            # the index of the duplicated elements
            dup_ind = np.where(trig_name_gw==dup_name)[0]
            alphabet = 0
            for i in dup_ind:
                trig_name_gw[i] += ascii_uppercase[alphabet]
                alphabet += 1
        # To store it in hdf5 file encoding is needed
        encode_trig_name_gw = np.array([name.encode() for name in trig_name_gw[:]])
        file['{}/name'.format(o)] = encode_trig_name_gw
        file['{}/gps'.format(o)] = time_gw[gwidx]

There are  69398  triggers
There are  144659  triggers
There are  165953  triggers
There are  134479  triggers


In [36]:
with h5py.File('gw_candidate_correct_repeating.hdf') as f:
    for k in f.keys():
        print(len(f[k]['name']))
        print(len(f[k]['gps']))

69398
69398
144659
144659
165953
165953
134479
134479


# Write trigger files

In [40]:
for o in tqdm(['o1','o2','o3a','o3b']):
    direct = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/trigger/'
    try:
        shutil.rmtree(direct)
    except FileNotFoundError:
        pass
    os.mkdir(direct)
    
    gwidx = trigger(obrun=o)
    trig_name_gw = name_gw[gwidx]
    uniname, count = np.unique(trig_name_gw, return_counts=True)
    duplicate = uniname[count>1]
    #select those with duplicated names
    for dup_name in duplicate:
        # the index of the duplicated elements
        dup_ind = np.where(trig_name_gw==dup_name)[0]
        alphabet = 0
        # loop over a pair/triple/... of duplicated events
        for i in dup_ind:
            trig_name_gw[i] += ascii_uppercase[alphabet]
            alphabet += 1

            with open(direct+trig_name_gw[i]+'.ini', 'w') as t:
            #This line can't be cut into multiple lines or if fails with "string format" issues
                t.write(
        '[trigger]\nname=%s\nmass1=%f\nmass2=%f\nspin1z=%f\nspin2z=%f\ntrigger_time=%f\nstat=%e\nifar=%e\n' % 
                (trig_name_gw[i],
                 mass1[gwidx][i],
                 mass2[gwidx][i],
                 spin1z[gwidx][i],
                 spin2z[gwidx][i],
                 time_gw[gwidx][i],
                 stat[gwidx][i],
                 ifar[gwidx][i])
               )
                t.close()

  0%|                                                                                                                                             | 0/4 [00:00<?, ?it/s]

There are  69398  triggers


 25%|█████████████████████████████████▎                                                                                                   | 1/4 [00:02<00:06,  2.19s/it]

There are  144659  triggers


 50%|██████████████████████████████████████████████████████████████████▌                                                                  | 2/4 [00:11<00:12,  6.12s/it]

There are  165953  triggers


 75%|███████████████████████████████████████████████████████████████████████████████████████████████████▊                                 | 3/4 [00:23<00:09,  9.09s/it]

There are  134479  triggers


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:32<00:00,  8.10s/it]


# Make sh files

In [63]:
for o in ['o1','o2','o3a','o3b']:
    direct1 = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/sh/'
    try:
        shutil.rmtree(direct1)
    except FileNotFoundError:
        pass
    
    os.mkdir(direct1)
    
    direct = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/condorsub/'
    directerr = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/condorerr/'
    directout = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/condorout/'
    directlog = '/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/condorlog/'

    for d in [direct,directerr,directout,directlog]:
        try:
            shutil.rmtree(d)
        except FileNotFoundError:
            pass
        os.mkdir(d)
    
    gwidx = trigger(obrun=o)
    trig_name_gw = name_gw[gwidx]
    uniname, count = np.unique(trig_name_gw, return_counts=True)
    duplicate = uniname[count>1]
    #select those with duplicated names
    for dup_name in duplicate:
        # the index of the duplicated elements
        dup_ind = np.where(trig_name_gw==dup_name)[0]
        alphabet = 0
        # loop over a pair/triple/... of duplicated events
        for i in dup_ind:
            trig_name_gw[i] += ascii_uppercase[alphabet]
            alphabet += 1
            with open(direct1+trig_name_gw[i]+'.sh', 'w') as t:
                #This line can't be cut into multiple lines or if fails with "string format" issues
                t.write('pycbc_inference --verbose \
                --seed 19930309 \
                --config-file /work/yifan.wang/grb/git-notebooks/gwconfig/gwinference.ini \
                                /work/yifan.wang/grb/git-notebooks/gwconfig/'+str(o)+'.ini \
                                /work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/trigger/'+trig_name_gw[i]+'.ini \
                --output-file /work/yifan.wang/grb/gwrun/'+o+'/result/'+trig_name_gw[i]+'.hdf \
                --nprocesses 1 \
                --force\n\n')
                
            with open(direct+trig_name_gw[i]+'.sub', 'w') as t:
                t.write('universe = vanilla\n'+
            'accounting_group = cbc.imp.gwgrb\n'+
            'getenv = True\n'+
            'executable = /work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/sh/'+trig_name_gw[i]+'.sh\n'+
            'output = '+directout+trig_name_gw[i]+'.output\n'+
            'error = '+directerr+trig_name_gw[i]+'.err\n'+
            'log = '+directlog+trig_name_gw[i]+'.log\n'+
            'request_cpus = 1\n'+
            'request_memory = 8000\n'+
            'queue')

There are  69398  triggers
There are  144659  triggers
There are  165953  triggers
There are  134479  triggers


# Make DAG

In [64]:
for o in ['o1','o2','o3a','o3b']:
    with open('/work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/run.dag','w') as t:
        gwidx = trigger(obrun=o)
        trig_name_gw = name_gw[gwidx]
        uniname, count = np.unique(trig_name_gw, return_counts=True)
        duplicate = uniname[count>1]
        #select those with duplicated names
        for dup_name in duplicate:
            # the index of the duplicated elements
            dup_ind = np.where(trig_name_gw==dup_name)[0]
            alphabet = 0
            # loop over a pair/triple/... of duplicated events
            for i in dup_ind:
                trig_name_gw[i] += ascii_uppercase[alphabet]
                alphabet += 1
                t.write('JOB '+str(uuid.uuid4()).replace('-', '')+
                ' /work/yifan.wang/grb/gwrun/duplicated_names/'+o+'/condorsub/'+trig_name_gw[i]+'.sub\n')

There are  69398  triggers
There are  144659  triggers
There are  165953  triggers
There are  134479  triggers


# 0601: Check the failure runs

In [6]:
missing = {}
for o in ['o1','o2','o3a','o3b']:
    missing[o] = ''
    gwidx = trigger(obrun=o)
    with h5py.File('./gw_candidate_correct_repeating.hdf','r') as f:
        for name_i,name in enumerate(f[o]['name'][:]):
            name = name.decode()
            path = '/work/yifan.wang/grb/gwrun/'+o+'/result/'+name+'.hdf'
            if not os.path.exists(path):
                missing[o] += str(name)+'.err '

There are  69398  triggers
There are  144659  triggers
There are  165953  triggers
There are  134479  triggers


In [7]:
missing

{'o1': '150924_010939.err 150925_001827.err 150925_001847.err 150926_182243.err 150927_214051.err 150928_091942.err 151210_164302.err 160115_024708.err ',
 'o2': '161210_023712.err 170208_153103.err 170215_184250.err 170217_015845.err 170303_234307.err 170315_021853.err 170324_204819.err 170411_135955.err 170420_160002.err 170420_203024.err 170626_193337.err 170705_211541.err 170721_195834.err 170813_065940.err 170825_215946.err ',
 'o3a': '190401_150055.err 190401_150313.err 190419_140055.err 190419_140110.err 190825_201603.err ',
 'o3b': '191101_150218.err 191110_101501.err 191202_040227.err 200129_010431.err 200323_193021.err 200323_193126.err 200323_193147.err '}

# Cut out the failed runs

In [24]:
with h5py.File('./gw_candidate_prod.hdf','w') as f2:
    with h5py.File('./gw_candidate_correct_repeating.hdf','r') as f:
        for o in ['o1','o2','o3a','o3b']:
            gwidx = trigger(obrun=o)
            fail_idx = []
            allindex = range(len(f[o]['name'][:]))
            for name_i,name in enumerate(f[o]['name'][:]):
                name = name.decode()
                path = '/work/yifan.wang/grb/gwrun/'+o+'/result/'+name+'.hdf'
                if not os.path.exists(path):
                    fail_idx.append(name_i)
            print('failed runs length: ',len(fail_idx),', index: ', fail_idx)
            gwidx_cut = np.delete(allindex,fail_idx)
            print('After checking failed runs, there are ',len(gwidx_cut), ' triggers\n')
            f2['{}/name'.format(o)] = f[o]['name'][gwidx_cut]
            f2['{}/gps'.format(o)] = f[o]['gps'][gwidx_cut]

There are  69398  triggers
failed runs length:  8 , index:  [5827, 6386, 6387, 7850, 8784, 9027, 52123, 68444]
After checking failed runs, there are  69390  triggers

There are  144659  triggers
failed runs length:  15 , index:  [2712, 25385, 30914, 31886, 43377, 51766, 59896, 75197, 81969, 81970, 108404, 116518, 120160, 134014, 144658]
After checking failed runs, there are  144644  triggers

There are  165953  triggers
failed runs length:  5 , index:  [0, 1, 14603, 14604, 129013]
After checking failed runs, there are  165948  triggers

There are  134479  triggers
failed runs length:  7 , index:  [0, 6371, 24254, 70445, 131026, 131027, 131028]
After checking failed runs, there are  134472  triggers



In [25]:
f = h5py.File('gw_candidate_prod.hdf','r')

In [29]:
f['o2']['name']

<HDF5 dataset "name": shape (144644,), type "|S14">

In [30]:
f.close()